In [1]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

In [2]:
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)

    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding="same",
        activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)

    predictions = {
        # Generate predictions (for PREDICT and EVAL mode)
        "classes": tf.argmax(input=logits, axis=1),
        # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
        # `logging_hook`.
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
            labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [5]:
def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
        model_fn=cnn_model_fn, model_dir="mnist_convnet_model")
    
    # Set up logging for predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(
        tensors=tensors_to_log, every_n_iter=50)
    
    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])
    
    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

In [6]:
if __name__ == "__main__":
      tf.app.run()

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f817d079a20>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Restoring parameters from mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Saving checkpoints for 20001 into mnist_convnet_model/model.ckpt.
INFO:tensorflow:pro

INFO:tensorflow:loss = 0.09480389, step = 20001
INFO:tensorflow:probabilities = [[0.00000378 0.99144953 0.00004662 0.00138577 0.00030169 0.00010823
  0.00020532 0.00006836 0.00522082 0.00120987]
 [0.00003223 0.00000004 0.00000126 0.99634534 0.         0.00271809
  0.         0.00008255 0.0000003  0.00082005]
 [0.97983277 0.00000378 0.01651951 0.00188078 0.00000073 0.00133439
  0.00001247 0.00001412 0.00001811 0.00038331]
 [0.00000506 0.00047194 0.00017798 0.894139   0.00006953 0.03592737
  0.00000416 0.00136021 0.02782145 0.04002335]
 [0.00002187 0.00773355 0.00043875 0.00078087 0.00000384 0.00000279
  0.00000007 0.98785406 0.00006554 0.00309859]
 [0.00248819 0.00737868 0.01105206 0.04839297 0.011268   0.04605795
  0.7990778  0.00003849 0.07418613 0.00005966]
 [0.9958079  0.00000046 0.00014986 0.00018864 0.00015421 0.00021746
  0.00169017 0.00004829 0.00049099 0.001252  ]
 [0.00000568 0.00003605 0.00012616 0.98309267 0.00001856 0.00065909
  0.00000016 0.0000882  0.00012481 0.01584867]


INFO:tensorflow:global_step/sec: 129.455
INFO:tensorflow:probabilities = [[0.00002672 0.00000032 0.00000979 0.00657625 0.00002516 0.9899607
  0.00000082 0.0000068  0.0002101  0.00318337]
 [0.00000683 0.00000078 0.9997669  0.00008845 0.         0.00000006
  0.         0.0000761  0.00006088 0.00000005]
 [0.99970764 0.         0.00002173 0.00000027 0.         0.00022294
  0.00000001 0.00000027 0.00001346 0.00003364]
 [0.99804014 0.00000019 0.00086747 0.00000644 0.00000546 0.00030185
  0.00006339 0.00000549 0.00002326 0.00068632]
 [0.9990233  0.00000004 0.00043713 0.00002513 0.00000797 0.00001403
  0.0000081  0.00003683 0.00000156 0.00044595]
 [0.00000034 0.00001674 0.00000409 0.9982747  0.00000227 0.00124294
  0.00000007 0.00014091 0.00002744 0.00029048]
 [0.99990416 0.         0.00000387 0.0000022  0.00000102 0.0000427
  0.00000886 0.00000014 0.00001949 0.00001761]
 [0.01423797 0.00001515 0.00080453 0.00011555 0.00047687 0.00590404
  0.9703269  0.00000032 0.00800056 0.0001181 ]
 [0.00000

INFO:tensorflow:loss = 0.112565756, step = 20101 (0.773 sec)
INFO:tensorflow:probabilities = [[0.00272191 0.00001595 0.86830676 0.11651774 0.00137126 0.00006151
  0.00099195 0.00771088 0.00194943 0.00035263]
 [0.00005558 0.00000146 0.00656602 0.0038103  0.00006364 0.00052366
  0.00000228 0.00004948 0.9873453  0.00158226]
 [0.00000061 0.9990396  0.00003663 0.00009786 0.00005208 0.00000296
  0.00001442 0.00035975 0.00029915 0.00009691]
 [0.00000737 0.00055698 0.98456144 0.00752641 0.00011777 0.0000314
  0.00014159 0.00036618 0.00666238 0.00002855]
 [0.00000296 0.00000016 0.99993455 0.00005693 0.00000025 0.00000094
  0.00000004 0.00000196 0.00000185 0.0000003 ]
 [0.00070177 0.00000026 0.00027064 0.00000661 0.00039793 0.00000821
  0.9985764  0.0000002  0.00002528 0.00001274]
 [0.00000257 0.00026774 0.00001759 0.06409699 0.00002258 0.92987007
  0.00001549 0.00000623 0.00366508 0.00203567]
 [0.000015   0.00000165 0.00002906 0.00002199 0.00002629 0.00002977
  0.00000143 0.00000026 0.99984443 

INFO:tensorflow:global_step/sec: 142.456
INFO:tensorflow:probabilities = [[0.00000845 0.00000109 0.00000228 0.0000058  0.00002847 0.00854289
  0.98959774 0.00000001 0.00181254 0.00000071]
 [0.0014499  0.00748877 0.00193834 0.00325992 0.0037869  0.02303417
  0.9511518  0.00005629 0.00741583 0.00041811]
 [0.00228589 0.01328828 0.00732846 0.00984018 0.0295615  0.82584167
  0.00301051 0.07205121 0.02034843 0.01644389]
 [0.00000078 0.00000474 0.00004887 0.9998472  0.         0.00006113
  0.         0.00000332 0.00002489 0.0000091 ]
 [0.00010211 0.9920282  0.00063119 0.00094265 0.00172669 0.00019856
  0.00028608 0.0033045  0.0006278  0.0001523 ]
 [0.6620851  0.00048089 0.01752836 0.02120902 0.11777697 0.02447341
  0.02480077 0.0217643  0.03424493 0.07563616]
 [0.00000439 0.00021102 0.00029224 0.00019945 0.98968166 0.00021699
  0.00004064 0.0015009  0.00008946 0.00776338]
 [0.00000116 0.00000002 0.0052812  0.00014767 0.00000222 0.00000006
  0.         0.9941993  0.00007096 0.00029748]
 [0.000

...

INFO:tensorflow:global_step/sec: 141.141
INFO:tensorflow:probabilities = [[0.00000043 0.00000034 0.999969   0.00000381 0.00001255 0.00000001
  0.00000037 0.00000097 0.00000028 0.00001219]
 [0.00000059 0.00000375 0.00004421 0.0000131  0.0006128  0.0000014
  0.00000024 0.9977863  0.0000081  0.00152957]
 [0.00002111 0.00064821 0.9972631  0.00067168 0.00109672 0.00003394
  0.00000213 0.00012357 0.00011013 0.0000294 ]
 [0.00002502 0.00001985 0.00036724 0.00267232 0.02454353 0.00121768
  0.00002655 0.0003538  0.00212469 0.9686493 ]
 [0.00000002 0.99994576 0.00001508 0.00001211 0.00000128 0.00000042
  0.00000037 0.00000004 0.00002437 0.0000005 ]
 [0.0000008  0.00001457 0.00054875 0.00066151 0.00000019 0.00000007
  0.         0.998678   0.00000735 0.00008874]
 [0.00001309 0.9979103  0.00011168 0.00013551 0.00011033 0.00000383
  0.00004169 0.00085001 0.0007128  0.0001107 ]
 [0.00000056 0.         0.         0.00000005 0.00000018 0.00002299
  0.         0.9999577  0.00000036 0.00001826]
 [0.0000

INFO:tensorflow:loss = 0.04089845, step = 39901 (0.709 sec)
INFO:tensorflow:probabilities = [[0.         0.00000032 0.9999981  0.00000013 0.00000095 0.
  0.00000004 0.00000028 0.00000008 0.        ]
 [0.00003341 0.00000439 0.9944027  0.00471455 0.00000763 0.00000255
  0.00000005 0.00042177 0.00039249 0.00002048]
 [0.00000241 0.00056742 0.00059126 0.9982529  0.00000226 0.00008354
  0.00000003 0.00007551 0.00027529 0.00014937]
 [0.00000002 0.00002037 0.99971193 0.00001184 0.00000096 0.00000001
  0.00000007 0.0000101  0.00024478 0.00000001]
 [0.999271   0.00002228 0.00003432 0.00000189 0.00002493 0.00015969
  0.00033926 0.00012661 0.00000651 0.00001352]
 [0.00000503 0.0001926  0.00015032 0.99288744 0.00000351 0.00561695
  0.00000447 0.00001486 0.0001634  0.00096133]
 [0.00000005 0.00000047 0.         0.0021361  0.00000121 0.9949811
  0.         0.00000107 0.00008685 0.00279311]
 [0.00001049 0.00744727 0.00004914 0.00266978 0.8948404  0.00244977
  0.00003988 0.00903626 0.00009755 0.0833594

INFO:tensorflow:Saving checkpoints for 40000 into mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.09811858.
INFO:tensorflow:Starting evaluation at 2018-03-05-08:25:11
INFO:tensorflow:Restoring parameters from mnist_convnet_model/model.ckpt-40000
INFO:tensorflow:Finished evaluation at 2018-03-05-08:25:11
INFO:tensorflow:Saving dict for global step 40000: accuracy = 0.9803, global_step = 40000, loss = 0.061217446
{'accuracy': 0.9803, 'loss': 0.061217446, 'global_step': 40000}


SystemExit: 

/usr/local/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
